In [8]:
import pandas as pd
import influxdb_client
from influxdb_client import Point
from influxdb_client.client.write_api import SYNCHRONOUS
import pathlib
import subprocess
import os

# Secrets
token = ""
url = "https://iwi-i-influx-db-01.hs-karlsruhe.de:8086"
bucket = "iot_gebaeude_am"
org = "Vorlesung"

# Client erstellen und Read/Write API anlegen
write_client = influxdb_client.InfluxDBClient(url=url, token=token, org=org)
write_api = write_client.write_api(write_options=SYNCHRONOUS)
query_api = write_client.query_api()



In [9]:
df_a = pd.read_parquet("data/aggregated_data/output.parquet")


date_time device_id    tmp    hum  CO2  VOC  vis   IR  WIFI  \
0      2022-10-10 14:09:26      a014  21.10  55.26  528  450  488   61     2   
1      2022-10-10 14:18:26      a014  22.37  51.95  526  450  528   72     2   
2      2022-10-10 14:18:47      a014  22.44  51.73  525  450  647  102     2   
3      2022-10-10 14:19:07      a014  22.50  51.63  525  450  766  130     2   
4      2022-10-10 14:19:26      a014  22.56  51.41  526  450  877  157     1   
...                    ...       ...    ...    ...  ...  ...  ...  ...   ...   
216317 2023-10-01 22:50:26      a112  23.46  49.09  483  987    7    0     1   
216318 2023-10-01 23:05:35      a112  23.45  49.22  483  926    9    2     2   
216319 2023-10-01 23:20:42      a112  23.42  49.28  484  957    7    1     1   
216320 2023-10-01 23:35:50      a112  23.39  49.41  490  930   10    3     2   
216321 2023-10-01 23:50:57      a112  23.36  49.50  493  954    7    2     2   

        BLE  rssi  channel_rssi   snr       gateway  channel_index  \
0         3   -63           -63   8.2  drag-lps8-01              1   
1         2   -55           -55   8.2  drag-lps8-01              4   
2         1   -57           -57   6.8  drag-lps8-01              5   
3         1   -55           -55   8.5  drag-lps8-01              6   
4         1   -59           -59   8.5  drag-lps8-01              7   
...     ...   ...           ...   ...           ...            ...   
216317    0  -124          -124 -17.5  drag-lps8-02              3   
216318    2  -114          -114  -4.8  drag-outd-01              5   
216319    0  -124          -124  -9.2  drag-lps8-02              4   
216320    2  -113          -113  -3.8  drag-outd-01              6   
216321    2  -120          -120  -3.2  drag-lps8-08              0   

        spreading_factor  bandwidth  f_cnt  
0                      7     125000      2  
1                      7     125000      3  
2                      7     125000      4  
3                      7     125000      5  
4                      7     125000      6  
...                  ...        ...    ...  
216317                11     125000  44667  
216318                11     125000  44668  
216319                11     125000  44669  
216320                11     125000  44670  
216321                11     125000  44671  

[216322 rows x 18 columns]

1,20 min für 500 datenpunkte

In [15]:
for index, row in df_a.loc[df_a["device_id"] == "a014"].iterrows():
    timestamp = row['date_time']  # Annahme, dass die Spalte 'timestamp' existiert
    if index % 500 == 0:
        print(f"Index {index}: Dies ist eine Nachricht.")
    for key, value in row.to_dict().items():
        if key != 'date_time':  # Überspringe die Zeitstempel-Spalte
            point = Point(f"{index}_{key}")
            point.tag("sensor", f"{index}")
            point.field("value", value)
            point.time(timestamp)  # Setze den Zeitstempel
            write_api.write(bucket=bucket, org=org, record=point)

Index 0: Dies ist eine Nachricht.
Index 500: Dies ist eine Nachricht.
Index 1000: Dies ist eine Nachricht.
Index 1500: Dies ist eine Nachricht.
Index 2000: Dies ist eine Nachricht.
Index 2500: Dies ist eine Nachricht.
Index 3000: Dies ist eine Nachricht.
Index 3500: Dies ist eine Nachricht.


In [16]:
column_names = ["device_id","tmp","hum",
                "CO2","VOC","vis","IR","WIFI",
                "BLE","rssi","channel_rssi","snr","gateway",
                "channel_index","spreading_factor","bandwidth","f_cnt"
]
# Define the query
#query = f"""from(bucket: "{bucket}") |> range(start: -1h)"""  # Adjust the query as needed

query = f"""from(bucket: "{bucket}")
 |> range(start: 2021-03-17T23:30:00Z)"""

tables = query_api.query(query, org=org)

data = []
for table in tables:
    for record in table.records:
        # Extract the necessary fields
        time = record.get_time()
        value = record.get_value()
        measurement = record.values.get('_measurement')
        field = record.values.get('_field')
        sensor = record.values.get('sensor')
        
        # Append to data list
        data.append([time, value, measurement, field, sensor])

# Define column names
column_names = ['date_time', 'value', 'measurement', 'field', 'sensor']

# Create the DataFrame
df = pd.DataFrame(data, columns=column_names)

print(df)

                      date_time  value         measurement  field sensor
0     2022-10-10 14:09:26+00:00      3               0_BLE  value      0
1     2022-10-10 14:09:26+00:00    528               0_CO2  value      0
2     2022-10-10 14:09:26+00:00     61                0_IR  value      0
3     2022-10-10 14:09:26+00:00    450               0_VOC  value      0
4     2022-10-10 14:09:26+00:00      2              0_WIFI  value      0
...                         ...    ...                 ...    ...    ...
62062 2022-10-10 14:23:26+00:00    -57              9_rssi  value      9
62063 2022-10-10 14:23:26+00:00    8.0               9_snr  value      9
62064 2022-10-10 14:23:26+00:00      7  9_spreading_factor  value      9
62065 2022-10-10 14:23:26+00:00  23.18               9_tmp  value      9
62066 2022-10-10 14:23:26+00:00   1532               9_vis  value      9

[62067 rows x 5 columns]


In [91]:
df.to_csv("influx.csv")

In [2]:
df = pd.read_csv("influx.csv")
df

Unnamed: 0                  date_time  value         measurement field  \
0            0  2023-03-18 00:13:10+00:00    6.0  environmental_data   BLE   
1            1  2023-03-18 00:28:19+00:00    6.0  environmental_data   BLE   
2            2  2023-03-18 00:43:25+00:00    6.0  environmental_data   BLE   
3            3  2023-03-18 00:58:31+00:00    0.0  environmental_data   BLE   
4            4  2023-03-18 01:13:38+00:00    6.0  environmental_data   BLE   
..         ...                        ...    ...                 ...   ...   
70          70  2023-03-18 00:13:10+00:00    6.0  environmental_data   vis   
71          71  2023-03-18 00:28:19+00:00    6.0  environmental_data   vis   
72          72  2023-03-18 00:43:25+00:00    6.0  environmental_data   vis   
73          73  2023-03-18 00:58:31+00:00    6.0  environmental_data   vis   
74          74  2023-03-18 01:13:38+00:00    6.0  environmental_data   vis   

    sensor  
0      NaN  
1      NaN  
2      NaN  
3      NaN  
4      NaN  
..     ...  
70     NaN  
71     NaN  
72     NaN  
73     NaN  
74     NaN  

[75 rows x 6 columns]

In [ ]:
df_new = []
for time in df['date_time'].unique():
    df_time = df.loc[df['date_time'] == time]
    tmp = df_time[df_time['field'] == 'tmp']['value'].values[0]
    CO2 = df_time[df_time['field'] == 'CO2']['value'].values[0]
    BLE = df_time[df_time['field'] == 'BLE']['value'].values[0]
    IR = df_time[df_time['field'] == 'IR']['value'].values[0]
    WIFI = df_time[df_time['field'] == 'WIFI']['value'].values[0]
    VOC = df_time[df_time['field'] == 'VOC']['value'].values[0]
    bandwidth = df_time[df_time['field'] == 'bandwidth']['value'].values[0]
    channel_index = df_time[df_time['field'] == 'channel_index']['value'].values[0]
    channel_rssi = df_time[df_time['field'] == 'channel_rssi']['value'].values[0]
    f_cnt = df_time[df_time['field'] == 'f_cnt']['value'].values[0]
    hum = df_time[df_time['field'] == 'hum']['value'].values[0]
    rssi = df_time[df_time['field'] == 'rssi']['value'].values[0]
    spreading_factor = df_time[df_time['field'] == 'spreading_factor']['value'].values[0]
    vis = df_time[df_time['field'] == 'vis']['value'].values[0]
    device_id = df_time[df_time['field'] == 'device_id']['value'].values[0]
    snr = df_time[df_time['field'] == 'snr']['value'].values[0]
    gateway = df_time[df_time['field'] == 'gateway']['value'].values[0]
    df_new.append([time, device_id, tmp, hum, CO2, VOC, vis, IR, WIFI, BLE, rssi, channel_rssi, snr, gateway, channel_index, spreading_factor, bandwidth, f_cnt])
df_new = pd.DataFrame(df_new, columns=['date_time', 'device_id', 'tmp', 'hum', 'CO2', 'VOC', 'vis', 'IR', 'WIFI', 'BLE', 'rssi', 'channel_rssi', 'snr', 'gateway', 'channel_index', 'spreading_factor', 'bandwidth', 'f_cnt'])


In [42]:
df_new = []
fields = ['tmp', 'CO2', 'BLE', 'IR', 'WIFI', 'VOC', 'bandwidth', 'channel_index', 'channel_rssi', 'f_cnt', 'hum', 'rssi', 'spreading_factor', 'vis', 'device_id', 'snr', 'gateway']
for time in df['date_time'].unique():
    df_time = df.loc[df['date_time'] == time]
    print(df_time)
    row = [time]
    for field in fields:        
        row.append(df_time[df_time['measurement'].str.contains(field)]['value'].tolist()[0])

    df_new.append(row)

df_new = pd.DataFrame(df_new, columns=['date_time'] + fields)
df_new

                   date_time         value         measurement  field sensor
0  2022-10-10 14:09:26+00:00             3               0_BLE  value      0
1  2022-10-10 14:09:26+00:00           528               0_CO2  value      0
2  2022-10-10 14:09:26+00:00            61                0_IR  value      0
3  2022-10-10 14:09:26+00:00           450               0_VOC  value      0
4  2022-10-10 14:09:26+00:00             2              0_WIFI  value      0
5  2022-10-10 14:09:26+00:00        125000         0_bandwidth  value      0
6  2022-10-10 14:09:26+00:00             1     0_channel_index  value      0
7  2022-10-10 14:09:26+00:00           -63      0_channel_rssi  value      0
8  2022-10-10 14:09:26+00:00          a014         0_device_id  value      0
9  2022-10-10 14:09:26+00:00             2             0_f_cnt  value      0
10 2022-10-10 14:09:26+00:00  drag-lps8-01           0_gateway  value      0
11 2022-10-10 14:09:26+00:00         55.26               0_hum  value      0

[[Timestamp('2022-10-10 14:09:26+0000', tz='tzutc()'),
  21.1,
  528,
  3,
  61,
  2,
  450,
  125000,
  1,
  -63,
  2,
  55.26,
  -63,
  7,
  488,
  'a014',
  8.2,
  'drag-lps8-01'],
 [Timestamp('2022-10-18 01:33:49+0000', tz='tzutc()'),
  22.81,
  505,
  0,
  3,
  2,
  719,
  125000,
  4,
  -65,
  1116,
  56.41,
  -65,
  7,
  10,
  'a014',
  9.2,
  'drag-lps8-01'],
 [Timestamp('2022-10-18 01:48:55+0000', tz='tzutc()'),
  22.8,
  511,
  0,
  0,
  1,
  699,
  125000,
  2,
  -67,
  1117,
  56.35,
  -67,
  7,
  7,
  'a014',
  7.5,
  'drag-lps8-01'],
 [Timestamp('2022-10-18 02:04:02+0000', tz='tzutc()'),
  22.81,
  505,
  0,
  3,
  2,
  721,
  125000,
  6,
  -64,
  1118,
  56.35,
  -64,
  7,
  10,
  'a014',
  8.2,
  'drag-lps8-01'],
 [Timestamp('2022-10-18 02:19:15+0000', tz='tzutc()'),
  22.79,
  511,
  0,
  0,
  1,
  707,
  125000,
  7,
  -69,
  1120,
  56.38,
  -69,
  7,
  7,
  'a014',
  9.5,
  'drag-lps8-01'],
 [Timestamp('2022-10-18 02:34:23+0000', tz='tzutc()'),
  22.79,
  514,
  0,

In [47]:
df_new

date_time    tmp  CO2  BLE   IR  WIFI  VOC  bandwidth  \
0    2022-10-10 14:09:26+00:00  21.10  528    3   61     2  450     125000   
1    2022-10-18 01:33:49+00:00  22.81  505    0    3     2  719     125000   
2    2022-10-18 01:48:55+00:00  22.80  511    0    0     1  699     125000   
3    2022-10-18 02:04:02+00:00  22.81  505    0    3     2  721     125000   
4    2022-10-18 02:19:15+00:00  22.79  511    0    0     1  707     125000   
...                        ...    ...  ...  ...  ...   ...  ...        ...   
3646 2022-10-18 00:48:28+00:00  22.80  498    0    0     2  831     125000   
3647 2022-10-18 01:03:34+00:00  22.82  502    0    2     2  741     125000   
3648 2022-10-18 01:18:43+00:00  22.80  509    0    0     2  804     125000   
3649 2022-10-11 05:05:38+00:00  23.94  501    0    0     0  604     125000   
3650 2022-10-10 14:23:26+00:00  23.18  523    2  316     2  450     125000   

      channel_index  channel_rssi  f_cnt    hum  rssi  spreading_factor   vis  \
0                 1           -63      2  55.26   -63                 7   488   
1                 4           -65   1116  56.41   -65                 7    10   
2                 2           -67   1117  56.35   -67                 7     7   
3                 6           -64   1118  56.35   -64                 7    10   
4                 7           -69   1120  56.38   -69                 7     7   
...             ...           ...    ...    ...   ...               ...   ...   
3646              0           -66   1113  56.91   -66                 7     7   
3647              3           -66   1114  56.70   -66                 7     7   
3648              5           -64   1115  56.57   -64                 7     7   
3649              2           -63    109  49.15   -63                 7     7   
3650              0           -57     11  49.47   -57                 7  1532   

     device_id  snr       gateway  
0         a014  8.2  drag-lps8-01  
1         a014  9.2  drag-lps8-01  
2         a014  7.5  drag-lps8-01  
3         a014  8.2  drag-lps8-01  
4         a014  9.5  drag-lps8-01  
...        ...  ...           ...  
3646      a014  8.5  drag-lps8-01  
3647      a014  9.2  drag-lps8-01  
3648      a014  7.2  drag-lps8-01  
3649      a014  7.2  drag-lps8-01  
3650      a014  8.0  drag-lps8-01  

[3651 rows x 18 columns]

In [50]:
df_new_without_room_014 = pd.read_parquet("data/aggregated_data/output.parquet")
df_new_without_room_014 = df_new_without_room_014[df_new_without_room_014['device_id'] != 'a014']
df_new_without_room_014

date_time device_id    tmp    hum  CO2  VOC  vis  IR  WIFI  \
3651   2022-10-20 11:41:43      a017  23.56  49.06  762  450  129  31     3   
3652   2022-10-20 11:56:50      a017  23.67  49.09  763  451  146  39     4   
3653   2022-10-20 12:11:57      a017  23.74  49.47  815  500  150  39     3   
3654   2022-10-20 12:27:03      a017  23.72  49.63  839  513  121  27     1   
3655   2022-10-20 12:42:10      a017  23.71  49.63  845  525  111  22     1   
...                    ...       ...    ...    ...  ...  ...  ...  ..   ...   
216317 2023-10-01 22:50:26      a112  23.46  49.09  483  987    7   0     1   
216318 2023-10-01 23:05:35      a112  23.45  49.22  483  926    9   2     2   
216319 2023-10-01 23:20:42      a112  23.42  49.28  484  957    7   1     1   
216320 2023-10-01 23:35:50      a112  23.39  49.41  490  930   10   3     2   
216321 2023-10-01 23:50:57      a112  23.36  49.50  493  954    7   2     2   

        BLE  rssi  channel_rssi   snr       gateway  channel_index  \
3651      7  -118          -118  -4.5  drag-lps8-07              7   
3652      8  -110          -110  -2.0  drag-lps8-07              1   
3653     17  -120          -120  -4.5  drag-lps8-07              0   
3654      3  -118          -118  -7.8  drag-outd-01              5   
3655      2  -112          -112   3.2  drag-outd-01              4   
...     ...   ...           ...   ...           ...            ...   
216317    0  -124          -124 -17.5  drag-lps8-02              3   
216318    2  -114          -114  -4.8  drag-outd-01              5   
216319    0  -124          -124  -9.2  drag-lps8-02              4   
216320    2  -113          -113  -3.8  drag-outd-01              6   
216321    2  -120          -120  -3.2  drag-lps8-08              0   

        spreading_factor  bandwidth  f_cnt  
3651                   7     125000      2  
3652                   7     125000      3  
3653                   7     125000      4  
3654                   7     125000      5  
3655                   7     125000      6  
...                  ...        ...    ...  
216317                11     125000  44667  
216318                11     125000  44668  
216319                11     125000  44669  
216320                11     125000  44670  
216321                11     125000  44671  

[212671 rows x 18 columns]

In [54]:
def make_tz_naive(timestamp):
    if timestamp.tzinfo is not None:
        return timestamp.tz_convert(None).tz_localize(None)
    return timestamp

In [58]:
df_new.head()

date_time    tmp  CO2  BLE  IR  WIFI  VOC  bandwidth  \
0 2022-10-10 14:09:26  21.10  528    3  61     2  450     125000   
1 2022-10-18 01:33:49  22.81  505    0   3     2  719     125000   
2 2022-10-18 01:48:55  22.80  511    0   0     1  699     125000   
3 2022-10-18 02:04:02  22.81  505    0   3     2  721     125000   
4 2022-10-18 02:19:15  22.79  511    0   0     1  707     125000   

   channel_index  channel_rssi  f_cnt    hum  rssi  spreading_factor  vis  \
0              1           -63      2  55.26   -63                 7  488   
1              4           -65   1116  56.41   -65                 7   10   
2              2           -67   1117  56.35   -67                 7    7   
3              6           -64   1118  56.35   -64                 7   10   
4              7           -69   1120  56.38   -69                 7    7   

  device_id  snr       gateway  
0      a014  8.2  drag-lps8-01  
1      a014  9.2  drag-lps8-01  
2      a014  7.5  drag-lps8-01  
3      a014  8.2  drag-lps8-01  
4      a014  9.5  drag-lps8-01

In [57]:
df_new['date_time'] = df_new['date_time'].apply(make_tz_naive)

In [59]:
df_new_test = pd.concat([df_new, df_new_without_room_014], ignore_index=True)
df_new_test

date_time    tmp  CO2  BLE  IR  WIFI  VOC  bandwidth  \
0      2022-10-10 14:09:26  21.10  528    3  61     2  450     125000   
1      2022-10-18 01:33:49  22.81  505    0   3     2  719     125000   
2      2022-10-18 01:48:55  22.80  511    0   0     1  699     125000   
3      2022-10-18 02:04:02  22.81  505    0   3     2  721     125000   
4      2022-10-18 02:19:15  22.79  511    0   0     1  707     125000   
...                    ...    ...  ...  ...  ..   ...  ...        ...   
216317 2023-10-01 22:50:26  23.46  483    0   0     1  987     125000   
216318 2023-10-01 23:05:35  23.45  483    2   2     2  926     125000   
216319 2023-10-01 23:20:42  23.42  484    0   1     1  957     125000   
216320 2023-10-01 23:35:50  23.39  490    2   3     2  930     125000   
216321 2023-10-01 23:50:57  23.36  493    2   2     2  954     125000   

        channel_index  channel_rssi  f_cnt    hum  rssi  spreading_factor  \
0                   1           -63      2  55.26   -63                 7   
1                   4           -65   1116  56.41   -65                 7   
2                   2           -67   1117  56.35   -67                 7   
3                   6           -64   1118  56.35   -64                 7   
4                   7           -69   1120  56.38   -69                 7   
...               ...           ...    ...    ...   ...               ...   
216317              3          -124  44667  49.09  -124                11   
216318              5          -114  44668  49.22  -114                11   
216319              4          -124  44669  49.28  -124                11   
216320              6          -113  44670  49.41  -113                11   
216321              0          -120  44671  49.50  -120                11   

        vis device_id   snr       gateway  
0       488      a014   8.2  drag-lps8-01  
1        10      a014   9.2  drag-lps8-01  
2         7      a014   7.5  drag-lps8-01  
3        10      a014   8.2  drag-lps8-01  
4         7      a014   9.5  drag-lps8-01  
...     ...       ...   ...           ...  
216317    7      a112 -17.5  drag-lps8-02  
216318    9      a112  -4.8  drag-outd-01  
216319    7      a112  -9.2  drag-lps8-02  
216320   10      a112  -3.8  drag-outd-01  
216321    7      a112  -3.2  drag-lps8-08  

[216322 rows x 18 columns]

In [60]:
df_new_test.date_time = pd.to_datetime(df_new_test.date_time)
df_new_test

date_time    tmp  CO2  BLE  IR  WIFI  VOC  bandwidth  \
0      2022-10-10 14:09:26  21.10  528    3  61     2  450     125000   
1      2022-10-18 01:33:49  22.81  505    0   3     2  719     125000   
2      2022-10-18 01:48:55  22.80  511    0   0     1  699     125000   
3      2022-10-18 02:04:02  22.81  505    0   3     2  721     125000   
4      2022-10-18 02:19:15  22.79  511    0   0     1  707     125000   
...                    ...    ...  ...  ...  ..   ...  ...        ...   
216317 2023-10-01 22:50:26  23.46  483    0   0     1  987     125000   
216318 2023-10-01 23:05:35  23.45  483    2   2     2  926     125000   
216319 2023-10-01 23:20:42  23.42  484    0   1     1  957     125000   
216320 2023-10-01 23:35:50  23.39  490    2   3     2  930     125000   
216321 2023-10-01 23:50:57  23.36  493    2   2     2  954     125000   

        channel_index  channel_rssi  f_cnt    hum  rssi  spreading_factor  \
0                   1           -63      2  55.26   -63                 7   
1                   4           -65   1116  56.41   -65                 7   
2                   2           -67   1117  56.35   -67                 7   
3                   6           -64   1118  56.35   -64                 7   
4                   7           -69   1120  56.38   -69                 7   
...               ...           ...    ...    ...   ...               ...   
216317              3          -124  44667  49.09  -124                11   
216318              5          -114  44668  49.22  -114                11   
216319              4          -124  44669  49.28  -124                11   
216320              6          -113  44670  49.41  -113                11   
216321              0          -120  44671  49.50  -120                11   

        vis device_id   snr       gateway  
0       488      a014   8.2  drag-lps8-01  
1        10      a014   9.2  drag-lps8-01  
2         7      a014   7.5  drag-lps8-01  
3        10      a014   8.2  drag-lps8-01  
4         7      a014   9.5  drag-lps8-01  
...     ...       ...   ...           ...  
216317    7      a112 -17.5  drag-lps8-02  
216318    9      a112  -4.8  drag-outd-01  
216319    7      a112  -9.2  drag-lps8-02  
216320   10      a112  -3.8  drag-outd-01  
216321    7      a112  -3.2  drag-lps8-08  

[216322 rows x 18 columns]

In [39]:
df_time[df_time['measurement'].str.contains("CO2")]['value'].tolist()[0]

523

In [44]:
df_new = pd.DataFrame(df_new, columns=['date_time'] + fields)
df_new

date_time    tmp  CO2  BLE   IR  WIFI  VOC  bandwidth  \
0    2022-10-10 14:09:26+00:00  21.10  528    3   61     2  450     125000   
1    2022-10-18 01:33:49+00:00  22.81  505    0    3     2  719     125000   
2    2022-10-18 01:48:55+00:00  22.80  511    0    0     1  699     125000   
3    2022-10-18 02:04:02+00:00  22.81  505    0    3     2  721     125000   
4    2022-10-18 02:19:15+00:00  22.79  511    0    0     1  707     125000   
...                        ...    ...  ...  ...  ...   ...  ...        ...   
3646 2022-10-18 00:48:28+00:00  22.80  498    0    0     2  831     125000   
3647 2022-10-18 01:03:34+00:00  22.82  502    0    2     2  741     125000   
3648 2022-10-18 01:18:43+00:00  22.80  509    0    0     2  804     125000   
3649 2022-10-11 05:05:38+00:00  23.94  501    0    0     0  604     125000   
3650 2022-10-10 14:23:26+00:00  23.18  523    2  316     2  450     125000   

      channel_index  channel_rssi  f_cnt    hum  rssi  spreading_factor   vis  \
0                 1           -63      2  55.26   -63                 7   488   
1                 4           -65   1116  56.41   -65                 7    10   
2                 2           -67   1117  56.35   -67                 7     7   
3                 6           -64   1118  56.35   -64                 7    10   
4                 7           -69   1120  56.38   -69                 7     7   
...             ...           ...    ...    ...   ...               ...   ...   
3646              0           -66   1113  56.91   -66                 7     7   
3647              3           -66   1114  56.70   -66                 7     7   
3648              5           -64   1115  56.57   -64                 7     7   
3649              2           -63    109  49.15   -63                 7     7   
3650              0           -57     11  49.47   -57                 7  1532   

     device_id  snr       gateway  
0         a014  8.2  drag-lps8-01  
1         a014  9.2  drag-lps8-01  
2         a014  7.5  drag-lps8-01  
3         a014  8.2  drag-lps8-01  
4         a014  9.5  drag-lps8-01  
...        ...  ...           ...  
3646      a014  8.5  drag-lps8-01  
3647      a014  9.2  drag-lps8-01  
3648      a014  7.2  drag-lps8-01  
3649      a014  7.2  drag-lps8-01  
3650      a014  8.0  drag-lps8-01  

[3651 rows x 18 columns]

In [26]:
similar_values = df_time[df_time['measurement'].str.contains("CO2")]['value']
similar_values

1    528
Name: value, dtype: object

In [95]:
df[df['date_time'] == "2023-03-18 00:13:10+00:00"]

Unnamed: 0                  date_time      value         measurement  \
0            0  2023-03-18 00:13:10+00:00       6.00  environmental_data   
5            5  2023-03-18 00:13:10+00:00     424.00  environmental_data   
10          10  2023-03-18 00:13:10+00:00       0.00  environmental_data   
15          15  2023-03-18 00:13:10+00:00    1032.00  environmental_data   
20          20  2023-03-18 00:13:10+00:00       2.00  environmental_data   
25          25  2023-03-18 00:13:10+00:00  125000.00  environmental_data   
30          30  2023-03-18 00:13:10+00:00       7.00  environmental_data   
35          35  2023-03-18 00:13:10+00:00    -103.00  environmental_data   
40          40  2023-03-18 00:13:10+00:00    6565.00  environmental_data   
45          45  2023-03-18 00:13:10+00:00       2.00  environmental_data   
50          50  2023-03-18 00:13:10+00:00      38.14  environmental_data   
55          55  2023-03-18 00:13:10+00:00    -103.00  environmental_data   
60          60  2023-03-18 00:13:10+00:00       8.00  environmental_data   
65          65  2023-03-18 00:13:10+00:00      19.80  environmental_data   
70          70  2023-03-18 00:13:10+00:00       6.00  environmental_data   

               field  sensor  
0                BLE     NaN  
5                CO2     NaN  
10                IR     NaN  
15               VOC     NaN  
20              WIFI     NaN  
25         bandwidth     NaN  
30     channel_index     NaN  
35      channel_rssi     NaN  
40             f_cnt     NaN  
45             floor     NaN  
50               hum     NaN  
55              rssi     NaN  
60  spreading_factor     NaN  
65               tmp     NaN  
70               vis     NaN

In [101]:
df_new = []
for time in df['date_time'].unique():
    df_time = df.loc[df['date_time'] == time]
    tmp = df_time[df_time['field'] == 'tmp']['value'].values[0]
    CO2 = df_time[df_time['field'] == 'CO2']['value'].values[0]
    BLE = df_time[df_time['field'] == 'BLE']['value'].values[0]
    IR = df_time[df_time['field'] == 'IR']['value'].values[0]
    WIFI = df_time[df_time['field'] == 'WIFI']['value'].values[0]
    VOC = df_time[df_time['field'] == 'VOC']['value'].values[0]
    bandwidth = df_time[df_time['field'] == 'bandwidth']['value'].values[0]
    channel_index = df_time[df_time['field'] == 'channel_index']['value'].values[0]
    channel_rssi = df_time[df_time['field'] == 'channel_rssi']['value'].values[0]
    f_cnt = df_time[df_time['field'] == 'f_cnt']['value'].values[0]
    hum = df_time[df_time['field'] == 'hum']['value'].values[0]
    rssi = df_time[df_time['field'] == 'rssi']['value'].values[0]
    spreading_factor = df_time[df_time['field'] == 'spreading_factor']['value'].values[0]
    vis = df_time[df_time['field'] == 'vis']['value'].values[0]
    device_id = df_time[df_time['field'] == 'device_id']['value'].values[0]
    snr = df_time[df_time['field'] == 'snr']['value'].values[0]
    gateway = df_time[df_time['field'] == 'gateway']['value'].values[0]
    df_new.append([time, device_id, tmp, hum, CO2, VOC, vis, IR, WIFI, BLE, rssi, channel_rssi, snr, gateway, channel_index, spreading_factor, bandwidth, f_cnt])
df_new = pd.DataFrame(df_new, columns=['date_time', 'device_id', 'tmp', 'hum', 'CO2', 'VOC', 'vis', 'IR', 'WIFI', 'BLE', 'rssi', 'channel_rssi', 'snr', 'gateway', 'channel_index', 'spreading_factor', 'bandwidth', 'f_cnt'])


In [102]:
df_new = pd.DataFrame(df_new, columns=['date_time', 'tmp', 'CO2', 'BLE', 'IR', 'WIFI', 'VOC', 'bandwidth', 'channel_index', 'channel_rssi', 'f_cnt', 'hum', 'rssi', 'spreading_factor', 'vis'])
df_new

date_time    tmp    CO2  BLE   IR  WIFI     VOC  bandwidth  \
0  2023-03-18 00:13:10+00:00  19.80  424.0  6.0  0.0   2.0  1032.0   125000.0   
1  2023-03-18 00:28:19+00:00  19.80  423.0  6.0  0.0   2.0   999.0   125000.0   
2  2023-03-18 00:43:25+00:00  19.80  423.0  6.0  0.0   2.0   970.0   125000.0   
3  2023-03-18 00:58:31+00:00  19.78  417.0  0.0  2.0   0.0   817.0   125000.0   
4  2023-03-18 01:13:38+00:00  19.81  426.0  6.0  0.0   2.0   883.0   125000.0   

   channel_index  channel_rssi   f_cnt    hum   rssi  spreading_factor  vis  
0            7.0        -103.0  6565.0  38.14 -103.0               8.0  6.0  
1            6.0        -102.0  6566.0  38.18 -102.0               8.0  6.0  
2            4.0        -102.0  6567.0  38.18 -102.0               8.0  6.0  
3            3.0        -105.0  6568.0  38.24 -105.0               8.0  6.0  
4            1.0        -101.0  6569.0  38.31 -101.0               8.0  6.0